# Comprehensive Time Series Analysis Example

This notebook demonstrates the full capabilities of the specialized-viz time series module, including:
1. Basic Time Series Analysis
2. Seasonal Decomposition
3. Pattern Detection
4. Advanced Analytics
5. Forecasting
6. Visualization

Let's start by importing the necessary libraries and setting up our environment.

In [6]:
# Import required libraries
import pandas as pd
import numpy as np
import yfinance as yf
import warnings
from specialized_viz.timeseries import (
    TimeseriesAnalysis,
    TimeseriesConfig,
    TimeseriesVisualizer,
    TimeseriesForecasting
)

# Set random seed for reproducibility
np.random.seed(42)

In [7]:
# Initialize analyzer with configuration
config = TimeseriesConfig(
    decomposition_method='additive',
    seasonal_periods=[5, 21, 63, 252],  # Daily, Weekly, Monthly, Yearly
    trend_window=20,
    forecast_horizon=30,
    cycle_max_period=252,  # One trading year
    anomaly_threshold=0.1

)

## 1. Load and Prepare Data


In [8]:
# Download sample data
ticker = 'AAPL'
stock_data = yf.download(ticker, start='2020-01-01', end='2023-12-31')
print(f"Downloaded {len(stock_data)} rows of data for {ticker}")
stock_data.head()
data_dict = {
    "Close": stock_data["Close"][ticker],
    "Open": stock_data["Open"][ticker],
    "High": stock_data["High"][ticker],
    "Low": stock_data["Low"][ticker],
    "Volume": stock_data["Volume"][ticker],
}
data = pd.DataFrame(data_dict)

[*********************100%***********************]  1 of 1 completed

Downloaded 1006 rows of data for AAPL


## 2. Basic Time Series Analysis
Let's analyze the components of our time series using decomposition.

In [9]:
# Initialize analyzer with configuration
config = TimeseriesConfig(
    decomposition_method='additive',
    seasonal_periods=[5, 21, 63, 252]  # Daily, Weekly, Monthly, Yearly
)
analyzer = TimeseriesAnalysis(data, config)

# Decompose the time series using daily seasonality (5 trading days)
decomposition = analyzer.decompose('Close', period=5)  # Using 5 for weekly trading pattern

# You can also analyze monthly seasonality
monthly_decomposition = analyzer.decompose('Close', period=21)  # Using 21 for monthly trading pattern

# Initialize visualizer
viz = TimeseriesVisualizer(analyzer)

# Plot decomposition
decomp_fig = viz.plot_decomposition('Close')
decomp_fig.show()

# Check for stationarity
stationarity = analyzer.analyze_stationarity('Close')
print("\nStationarity Analysis:")
print(f"ADF Test p-value: {stationarity['adf_test']['p_value']:.4f}")
print(f"Is stationary? {stationarity['adf_test']['is_stationary']}")


Stationarity Analysis:
ADF Test p-value: 0.5276
Is stationary? False


c:\apoorv\projects\specialized-viz\specialized_viz\timeseries\analysis.py:432: InterpolationWarning:

The test statistic is outside of the range of p-values available in the
look-up table. The actual p-value is smaller than the p-value returned.


c:\Users\belgu\anaconda3\envs\github\Lib\site-packages\numpy\_core\fromnumeric.py:57: FutureWarning:

'Series.swapaxes' is deprecated and will be removed in a future version. Please use 'Series.transpose' instead.



## 3. Time Series Decomposition
Let's decompose our series into trend, seasonal, and residual components.

In [10]:
# Perform decomposition
decomp_fig = viz.plot_decomposition('Close')
decomp_fig.show()

# Plot trend analysis
trend_fig = viz.plot_trend_analysis('Close')
trend_fig.show()

## 4. Pattern Analysis
Now let's analyze various patterns in our data.

In [11]:
# Seasonal Analysis
seasonality = analyzer.analyze_seasonality('Close')
print("\nSeasonality Analysis:")
print(f"Monthly Seasonal Strength: {seasonality.get('seasonal_strength_21', 0):.4f}")

# Print holiday effects
print("\nHoliday Effects:")
for holiday, effect in seasonality['holiday_effects'].items():
    print(f"{holiday}: {effect:.4f}")

# Cycle Analysis
cycles = analyzer.analyze_cycles('Close')
print("\nDominant Cycles (days):")
periodic_lengths = cycles['periodicity']['periodic_lengths']
correlation_strength = cycles['periodicity']['correlation_strength']
for length, strength in zip(periodic_lengths, correlation_strength):
    print(f"Period: {length} days, Strength: {strength:.4f}")

# Print Fourier analysis results
print("\nFourier Analysis - Top frequencies:")
frequencies = cycles['fourier']['dominant_frequencies']
amplitudes = cycles['fourier']['amplitudes']
for freq, amp in zip(frequencies, amplitudes):
    if freq != 0:  # Avoid division by zero
        period = 1/freq
        print(f"Period: {period:.1f} days, Amplitude: {amp:.4f}")
        
# Plot correlogram
corr_fig = viz.plot_correlogram('Close')
corr_fig.show()

# Distribution Evolution
dist_fig = viz.plot_distribution_evolution('Close')
dist_fig.show()

c:\apoorv\projects\specialized-viz\specialized_viz\timeseries\analysis.py:120: FutureWarning:

'Y' is deprecated and will be removed in a future version, please use 'YE' instead.




Seasonality Analysis:
Monthly Seasonal Strength: 0.0030

Holiday Effects:
is_weekend: 0.0000
month_end: 3.5674
fiscal_year_end: 13.5452

Dominant Cycles (days):
Period: 206 days, Strength: 0.5456
Period: 222 days, Strength: 0.5391
Period: 238 days, Strength: 0.5461

Fourier Analysis - Top frequencies:
Period: -503.0 days, Amplitude: 10884.4199
Period: 503.0 days, Amplitude: 10884.4199
Period: 1006.0 days, Amplitude: 14254.0809
Period: -1006.0 days, Amplitude: 14254.0809


c:\Users\belgu\anaconda3\envs\github\Lib\site-packages\numpy\_core\fromnumeric.py:57: FutureWarning:

'Series.swapaxes' is deprecated and will be removed in a future version. Please use 'Series.transpose' instead.



## 5. Change Point Detection and Anomaly Analysis
Let's identify significant changes and anomalies in our data.

In [12]:
# # Detect change points
# change_fig = viz.plot_change_points('Close')
# change_fig.show()

# # Detect anomalies
# anomalies = analyzer.detect_anomalies('Close')
# print("\nAnomalies detected by method:")
# for method, anomaly_series in anomalies.items():
#     print(f"{method}: {anomaly_series.sum()} anomalies")


## 6. Forecasting
Let's implement various forecasting methods and compare their performance.

In [13]:
# Create features and split data
forecaster = TimeseriesForecasting(data)
features = forecaster.create_features('Close')
train_size = int(len(features) * 0.8)
train_features = features[:train_size]
test_features = features[train_size:train_size+30]  # Take only 30 test samples
train_target = data['Close'][:train_size]
test_target = data['Close'][train_size:train_size+30]  # Take only 30 test samples

# Generate forecasts
seasonal_result = forecaster.seasonal_forecast(train_features, train_target)
sarima_result = forecaster.sarima_forecast(train_features, train_target)
ets_result = forecaster.ets_forecast(train_features, train_target)
combined_result = forecaster.combined_seasonal_forecast(train_features, train_target)


c:\Users\belgu\anaconda3\envs\github\Lib\site-packages\statsmodels\tsa\holtwinters\model.py:84: RuntimeWarning:

overflow encountered in matmul

c:\Users\belgu\anaconda3\envs\github\Lib\site-packages\statsmodels\tsa\holtwinters\model.py:84: RuntimeWarning:

overflow encountered in matmul



## 7. Model Evaluation and Comparison
Let's evaluate the performance of our different forecasting methods.

In [14]:
# Compare models
all_forecasts = {
    'Seasonal': seasonal_result['forecast'],
    'SARIMA': sarima_result['forecast'],
    'ETS': ets_result['forecast'],
    'Combined': combined_result['forecast']
}

# Evaluate each model
evaluation_results = {}
for model_name, forecast in all_forecasts.items():
    # Ensure forecast and test_target have same length
    common_index = forecast.index.intersection(test_target.index)
    metrics = forecaster.evaluate_forecast(
        forecast[common_index], 
        test_target[common_index]
    )
    evaluation_results[model_name] = metrics

comparison_df = pd.DataFrame(evaluation_results).round(4)
print("\nModel Comparison:")
print(comparison_df)



Model Comparison:
                      Seasonal   SARIMA       ETS  Combined
mse                   106.2450  83.8598  106.1151  106.6608
mae                     9.6666   8.4938    9.6587    9.6889
rmse                   10.3075   9.1575   10.3012   10.3277
r2                     -4.9853  -4.8181   -4.9779   -5.0087
mape                    5.9832   5.3122    5.9783    5.9972
smape                   6.1919   5.4797    6.1867    6.2068
directional_accuracy   46.4286  35.0000   42.8571   46.4286
mase                    6.4409   5.4848    6.4356    6.4558
nrmse                   0.6915   0.6804    0.6911    0.6928


## 8. Interactive Dashboard
Finally, let's create an interactive dashboard combining all our analyses.

In [15]:
# Create comprehensive dashboard
dashboard = viz.create_comprehensive_dashboard('Close')
dashboard.show()

c:\apoorv\projects\specialized-viz\specialized_viz\timeseries\analysis.py:120: FutureWarning:

'Y' is deprecated and will be removed in a future version, please use 'YE' instead.



## 9. Advanced Analytics
Let's perform some advanced analytics on our time series.

In [16]:
# Create animation of moving window analysis
animation_fig = viz.create_animation('Close')
animation_fig.show()

# Analyze feature importance
importance_fig = viz.plot_feature_importance(features, data['Close'])
importance_fig.show()

## 10. Online Learning and Adaptation
Finally, let's implement online learning to adapt to changing patterns.

In [17]:
# Implement online learning
forecaster.online_learning(features, data['Close'], window_size=63)

if hasattr(forecaster, 'performance_plot'):
    print("\nOnline Learning Performance Metrics:")
    print(forecaster.online_performance.describe().round(4))


Online Learning Performance Metrics:
         actual  predicted    error  drift_level
count   15.0000    15.0000  15.0000      15.0000
mean   138.0268   137.9225   1.7861       8.0000
std     34.6173    34.3468   2.0129       4.4721
min     59.5047    60.6809   0.0163       1.0000
25%    123.5322   125.8502   0.4857       4.5000
50%    139.6609   136.2347   1.3048       8.0000
75%    167.9379   167.5882   2.3225      11.5000
max    190.3667   190.0420   7.8648      15.0000


## Conclusion
This comprehensive analysis demonstrates the wide range of capabilities in the specialized-viz time series module. Key findings include:
1. Seasonal patterns in the data
2. Significant change points
3. Forecasting model performance
4. Feature importance
5. Adaptation to changing patterns